In [1]:
import pandas as pd
import numpy as np
import torch
import torch.nn as nn
from torch.utils.data import TensorDataset, DataLoader
from torch import Tensor
import torch.nn.functional as F
from torch.optim.lr_scheduler import MultiStepLR
from torch.utils.tensorboard import SummaryWriter

In [2]:
# Convolutional neural network (two convolutional layers)
class BiLSTM(nn.Module):
    def __init__(self, num_classes=4):
        super(BiLSTM, self).__init__()
           
        self.d1 = nn.Dropout(p=0.25)      
        self.bn1 = nn.BatchNorm1d(64,affine=False)
        self.ac1 = nn.Softplus()
        #self.rnn = nn.RNN(64,256,dropout=0.25)
        self.lstm = nn.LSTM(64,256,dropout=0.25,bidirectional=True)
        self.fc1 = nn.Linear(512, 64)
        self.fc2 = nn.Linear(64, num_classes)
        
    def forward(self, x):      
        x, _= self.lstm(x)
        #print(x.shape)
        x = x[:,-1,:]
        #print(x.shape)
        x = self.fc1(x)
        x = self.bn1(x)
        x = self.ac1(x)
        x = self.d1(x)
        x = self.fc2(x)

        return x

In [3]:
rnn = BiLSTM(4)
input = torch.randn(10, 64, 64)
output= rnn(input)
print(output.shape)

torch.Size([10, 4])


C:\Users\murray\anaconda3\envs\pytorchEEG\lib\site-packages\torch\nn\modules\rnn.py:62: UserWarning: dropout option adds dropout after all but last recurrent layer, so non-zero dropout expects num_layers greater than 1, but got dropout=0.25 and num_layers=1
  warnings.warn("dropout option adds dropout after all but last "


In [4]:
writer = SummaryWriter()

In [5]:
train_set = pd.read_csv("data/final_format/train_set.csv",header=None).to_numpy()
train_label = pd.read_csv("data/final_format/train_label.csv",header=None).to_numpy()
test_set = pd.read_csv("data/final_format/test_set.csv",header=None).to_numpy()
test_label = pd.read_csv("data/final_format/test_label.csv",header=None).to_numpy()

In [6]:
#delet first row data
train_set = train_set[1:]
train_label = train_label[1:]
test_set = test_set[1:]
test_label = test_label[1:]
print(train_set.shape, train_label.shape, test_set.shape, test_label.shape)

(14392, 4096) (14392, 1) (3598, 4096) (3598, 1)


In [7]:
train_label = train_label.reshape(-1)
test_label = test_label.reshape(-1)
print(train_set.shape, train_label.shape, test_set.shape, test_label.shape)

(14392, 4096) (14392,) (3598, 4096) (3598,)


In [8]:
#transpose to set data in time sequence
train_set = train_set.reshape(-1,64,64)
train_set = np.transpose(train_set,[0,2,1])
test_set = test_set.reshape(-1,64,64)
test_set = np.transpose(test_set,[0,2,1])
print(train_set.shape, train_label.shape, test_set.shape, test_label.shape)

(14392, 64, 64) (14392,) (3598, 64, 64) (3598,)


In [9]:
# Hyper parameters
num_epochs = 300
num_classes = 4
batch_size = 64
learning_rate = 1e-3

In [10]:
train_set_tensor = Tensor(train_set) 
train_label_tensor = Tensor(train_label).type(torch.LongTensor)

train_dataset = TensorDataset(train_set_tensor,train_label_tensor) 
train_loader = DataLoader(train_dataset, batch_size=batch_size) 

test_set_tensor = Tensor(test_set) 
test_label_tensor = Tensor(test_label).type(torch.LongTensor)

test_dataset = TensorDataset(test_set_tensor,test_label_tensor) 
test_loader = DataLoader(test_dataset, batch_size=batch_size) 

In [11]:
# Device configuration
device = torch.device('cuda:0' if torch.cuda.is_available() else 'cpu')
device

device(type='cuda', index=0)

In [12]:
model = BiLSTM(num_classes).to(device)

In [13]:
# Loss and optimizer
criterion = nn.CrossEntropyLoss()
optimizer = torch.optim.Adam(model.parameters(), lr=learning_rate, weight_decay=1e-3) 
#optimizer = torch.optim.Adam(model.parameters(), lr=learning_rate) 
milestones = [50,100,150,200,250]
milestones = [a * len(train_loader) for a in milestones]
scheduler = MultiStepLR(optimizer, milestones=milestones, gamma=0.5)

In [14]:
# Train the model
total_step = len(train_loader)
for epoch in range(num_epochs):
    correct=0
    total=0
    running_loss = 0
    for i, (X, Y) in enumerate(train_loader):
        X = X.to(device)
        Y = Y.to(device)
        
        
        # Forward pass
        outputs = model(X)
        loss = criterion(outputs, Y)
        
        # Backward and optimize
        optimizer.zero_grad()
        loss.backward()
        #scheduler.step() 
        #print(scheduler.get_last_lr()[0])
      
        optimizer.step()
        scheduler.step() 
        #print(optimizer.param_groups[0]["lr"])
        
        _, predicted = outputs.max(1)
        total += Y.size(0)
        correct += predicted.eq(Y).sum().item()
        running_loss += loss.item()
        accu=100.*correct/total
        train_loss = running_loss/(i+1)
        print ('Epoch [{}/{}], Step [{}/{}], Training Accuracy: {:.4f}%, Training Loss: {:.4f}%'.format(epoch+1, num_epochs, i+1, total_step, accu, train_loss))
    
   
        #writer.add_scalar(f'train/accuracy', accu, epoch)
        #writer.add_scalar(f'train/loss', train_loss, epoch)
        writer.add_scalars(f'train/accuracy_loss', {
            'accuracy': accu,
            'loss': train_loss,
        }, epoch)
        

Epoch [1/300], Step [1/225], Training Accuracy: 31.2500%, Training Loss: 1.4901%
Epoch [1/300], Step [2/225], Training Accuracy: 23.4375%, Training Loss: 1.5199%
Epoch [1/300], Step [3/225], Training Accuracy: 21.8750%, Training Loss: 1.5095%
Epoch [1/300], Step [4/225], Training Accuracy: 23.0469%, Training Loss: 1.5182%
Epoch [1/300], Step [5/225], Training Accuracy: 24.3750%, Training Loss: 1.5049%
Epoch [1/300], Step [6/225], Training Accuracy: 24.4792%, Training Loss: 1.5116%
Epoch [1/300], Step [7/225], Training Accuracy: 25.2232%, Training Loss: 1.5024%
Epoch [1/300], Step [8/225], Training Accuracy: 25.3906%, Training Loss: 1.5062%
Epoch [1/300], Step [9/225], Training Accuracy: 24.3056%, Training Loss: 1.5022%
Epoch [1/300], Step [10/225], Training Accuracy: 24.2188%, Training Loss: 1.4982%
Epoch [1/300], Step [11/225], Training Accuracy: 24.2898%, Training Loss: 1.4913%
Epoch [1/300], Step [12/225], Training Accuracy: 24.7396%, Training Loss: 1.4843%
Epoch [1/300], Step [13/2

Epoch [1/300], Step [114/225], Training Accuracy: 27.6864%, Training Loss: 1.4066%
Epoch [1/300], Step [115/225], Training Accuracy: 27.6630%, Training Loss: 1.4067%
Epoch [1/300], Step [116/225], Training Accuracy: 27.6266%, Training Loss: 1.4070%
Epoch [1/300], Step [117/225], Training Accuracy: 27.5908%, Training Loss: 1.4073%
Epoch [1/300], Step [118/225], Training Accuracy: 27.5159%, Training Loss: 1.4072%
Epoch [1/300], Step [119/225], Training Accuracy: 27.5079%, Training Loss: 1.4072%
Epoch [1/300], Step [120/225], Training Accuracy: 27.5000%, Training Loss: 1.4069%
Epoch [1/300], Step [121/225], Training Accuracy: 27.5310%, Training Loss: 1.4065%
Epoch [1/300], Step [122/225], Training Accuracy: 27.5102%, Training Loss: 1.4062%
Epoch [1/300], Step [123/225], Training Accuracy: 27.4644%, Training Loss: 1.4066%
Epoch [1/300], Step [124/225], Training Accuracy: 27.5076%, Training Loss: 1.4066%
Epoch [1/300], Step [125/225], Training Accuracy: 27.5375%, Training Loss: 1.4068%
Epoc

Epoch [2/300], Step [10/225], Training Accuracy: 30.0000%, Training Loss: 1.3570%
Epoch [2/300], Step [11/225], Training Accuracy: 29.9716%, Training Loss: 1.3601%
Epoch [2/300], Step [12/225], Training Accuracy: 30.5990%, Training Loss: 1.3574%
Epoch [2/300], Step [13/225], Training Accuracy: 30.7692%, Training Loss: 1.3591%
Epoch [2/300], Step [14/225], Training Accuracy: 31.1384%, Training Loss: 1.3593%
Epoch [2/300], Step [15/225], Training Accuracy: 31.4583%, Training Loss: 1.3583%
Epoch [2/300], Step [16/225], Training Accuracy: 32.2266%, Training Loss: 1.3518%
Epoch [2/300], Step [17/225], Training Accuracy: 32.3529%, Training Loss: 1.3545%
Epoch [2/300], Step [18/225], Training Accuracy: 32.1181%, Training Loss: 1.3548%
Epoch [2/300], Step [19/225], Training Accuracy: 31.8257%, Training Loss: 1.3555%
Epoch [2/300], Step [20/225], Training Accuracy: 31.9531%, Training Loss: 1.3547%
Epoch [2/300], Step [21/225], Training Accuracy: 31.9940%, Training Loss: 1.3520%
Epoch [2/300], S

Epoch [2/300], Step [110/225], Training Accuracy: 33.1676%, Training Loss: 1.3358%
Epoch [2/300], Step [111/225], Training Accuracy: 33.1503%, Training Loss: 1.3363%
Epoch [2/300], Step [112/225], Training Accuracy: 33.2031%, Training Loss: 1.3360%
Epoch [2/300], Step [113/225], Training Accuracy: 33.1582%, Training Loss: 1.3367%
Epoch [2/300], Step [114/225], Training Accuracy: 33.2100%, Training Loss: 1.3358%
Epoch [2/300], Step [115/225], Training Accuracy: 33.2065%, Training Loss: 1.3359%
Epoch [2/300], Step [116/225], Training Accuracy: 33.1762%, Training Loss: 1.3362%
Epoch [2/300], Step [117/225], Training Accuracy: 33.1731%, Training Loss: 1.3367%
Epoch [2/300], Step [118/225], Training Accuracy: 33.0906%, Training Loss: 1.3371%
Epoch [2/300], Step [119/225], Training Accuracy: 33.0620%, Training Loss: 1.3372%
Epoch [2/300], Step [120/225], Training Accuracy: 33.1641%, Training Loss: 1.3369%
Epoch [2/300], Step [121/225], Training Accuracy: 33.0966%, Training Loss: 1.3374%
Epoc

Epoch [3/300], Step [6/225], Training Accuracy: 29.9479%, Training Loss: 1.3564%
Epoch [3/300], Step [7/225], Training Accuracy: 30.8036%, Training Loss: 1.3541%
Epoch [3/300], Step [8/225], Training Accuracy: 31.0547%, Training Loss: 1.3446%
Epoch [3/300], Step [9/225], Training Accuracy: 31.2500%, Training Loss: 1.3467%
Epoch [3/300], Step [10/225], Training Accuracy: 30.9375%, Training Loss: 1.3467%
Epoch [3/300], Step [11/225], Training Accuracy: 30.8239%, Training Loss: 1.3460%
Epoch [3/300], Step [12/225], Training Accuracy: 31.5104%, Training Loss: 1.3397%
Epoch [3/300], Step [13/225], Training Accuracy: 31.3702%, Training Loss: 1.3403%
Epoch [3/300], Step [14/225], Training Accuracy: 31.0268%, Training Loss: 1.3452%
Epoch [3/300], Step [15/225], Training Accuracy: 31.2500%, Training Loss: 1.3453%
Epoch [3/300], Step [16/225], Training Accuracy: 31.9336%, Training Loss: 1.3396%
Epoch [3/300], Step [17/225], Training Accuracy: 31.9853%, Training Loss: 1.3380%
Epoch [3/300], Step 

...

Epoch [298/300], Step [146/225], Training Accuracy: 99.6682%, Training Loss: 0.0176%
Epoch [298/300], Step [147/225], Training Accuracy: 99.6705%, Training Loss: 0.0176%
Epoch [298/300], Step [148/225], Training Accuracy: 99.6727%, Training Loss: 0.0175%
Epoch [298/300], Step [149/225], Training Accuracy: 99.6644%, Training Loss: 0.0176%
Epoch [298/300], Step [150/225], Training Accuracy: 99.6667%, Training Loss: 0.0176%
Epoch [298/300], Step [151/225], Training Accuracy: 99.6689%, Training Loss: 0.0176%
Epoch [298/300], Step [152/225], Training Accuracy: 99.6711%, Training Loss: 0.0175%
Epoch [298/300], Step [153/225], Training Accuracy: 99.6732%, Training Loss: 0.0175%
Epoch [298/300], Step [154/225], Training Accuracy: 99.6753%, Training Loss: 0.0174%
Epoch [298/300], Step [155/225], Training Accuracy: 99.6774%, Training Loss: 0.0174%
Epoch [298/300], Step [156/225], Training Accuracy: 99.6795%, Training Loss: 0.0174%
Epoch [298/300], Step [157/225], Training Accuracy: 99.6815%, Tra

Epoch [299/300], Step [37/225], Training Accuracy: 99.7889%, Training Loss: 0.0174%
Epoch [299/300], Step [38/225], Training Accuracy: 99.7122%, Training Loss: 0.0182%
Epoch [299/300], Step [39/225], Training Accuracy: 99.6795%, Training Loss: 0.0188%
Epoch [299/300], Step [40/225], Training Accuracy: 99.6875%, Training Loss: 0.0187%
Epoch [299/300], Step [41/225], Training Accuracy: 99.6951%, Training Loss: 0.0185%
Epoch [299/300], Step [42/225], Training Accuracy: 99.7024%, Training Loss: 0.0186%
Epoch [299/300], Step [43/225], Training Accuracy: 99.7093%, Training Loss: 0.0184%
Epoch [299/300], Step [44/225], Training Accuracy: 99.7159%, Training Loss: 0.0185%
Epoch [299/300], Step [45/225], Training Accuracy: 99.7222%, Training Loss: 0.0183%
Epoch [299/300], Step [46/225], Training Accuracy: 99.7283%, Training Loss: 0.0184%
Epoch [299/300], Step [47/225], Training Accuracy: 99.7340%, Training Loss: 0.0182%
Epoch [299/300], Step [48/225], Training Accuracy: 99.6745%, Training Loss: 

Epoch [299/300], Step [158/225], Training Accuracy: 99.6934%, Training Loss: 0.0177%
Epoch [299/300], Step [159/225], Training Accuracy: 99.6954%, Training Loss: 0.0178%
Epoch [299/300], Step [160/225], Training Accuracy: 99.6973%, Training Loss: 0.0178%
Epoch [299/300], Step [161/225], Training Accuracy: 99.6894%, Training Loss: 0.0178%
Epoch [299/300], Step [162/225], Training Accuracy: 99.6914%, Training Loss: 0.0178%
Epoch [299/300], Step [163/225], Training Accuracy: 99.6933%, Training Loss: 0.0177%
Epoch [299/300], Step [164/225], Training Accuracy: 99.6951%, Training Loss: 0.0178%
Epoch [299/300], Step [165/225], Training Accuracy: 99.6970%, Training Loss: 0.0178%
Epoch [299/300], Step [166/225], Training Accuracy: 99.6988%, Training Loss: 0.0178%
Epoch [299/300], Step [167/225], Training Accuracy: 99.7006%, Training Loss: 0.0177%
Epoch [299/300], Step [168/225], Training Accuracy: 99.7024%, Training Loss: 0.0177%
Epoch [299/300], Step [169/225], Training Accuracy: 99.7041%, Tra

Epoch [300/300], Step [54/225], Training Accuracy: 99.8264%, Training Loss: 0.0159%
Epoch [300/300], Step [55/225], Training Accuracy: 99.8295%, Training Loss: 0.0160%
Epoch [300/300], Step [56/225], Training Accuracy: 99.8326%, Training Loss: 0.0161%
Epoch [300/300], Step [57/225], Training Accuracy: 99.8355%, Training Loss: 0.0161%
Epoch [300/300], Step [58/225], Training Accuracy: 99.8384%, Training Loss: 0.0160%
Epoch [300/300], Step [59/225], Training Accuracy: 99.8146%, Training Loss: 0.0162%
Epoch [300/300], Step [60/225], Training Accuracy: 99.8177%, Training Loss: 0.0163%
Epoch [300/300], Step [61/225], Training Accuracy: 99.8207%, Training Loss: 0.0161%
Epoch [300/300], Step [62/225], Training Accuracy: 99.7984%, Training Loss: 0.0163%
Epoch [300/300], Step [63/225], Training Accuracy: 99.8016%, Training Loss: 0.0162%
Epoch [300/300], Step [64/225], Training Accuracy: 99.8047%, Training Loss: 0.0162%
Epoch [300/300], Step [65/225], Training Accuracy: 99.7837%, Training Loss: 

Epoch [300/300], Step [174/225], Training Accuracy: 99.7216%, Training Loss: 0.0165%
Epoch [300/300], Step [175/225], Training Accuracy: 99.7232%, Training Loss: 0.0164%
Epoch [300/300], Step [176/225], Training Accuracy: 99.7248%, Training Loss: 0.0164%
Epoch [300/300], Step [177/225], Training Accuracy: 99.7263%, Training Loss: 0.0164%
Epoch [300/300], Step [178/225], Training Accuracy: 99.7191%, Training Loss: 0.0164%
Epoch [300/300], Step [179/225], Training Accuracy: 99.7207%, Training Loss: 0.0164%
Epoch [300/300], Step [180/225], Training Accuracy: 99.7222%, Training Loss: 0.0164%
Epoch [300/300], Step [181/225], Training Accuracy: 99.7238%, Training Loss: 0.0165%
Epoch [300/300], Step [182/225], Training Accuracy: 99.7167%, Training Loss: 0.0166%
Epoch [300/300], Step [183/225], Training Accuracy: 99.7182%, Training Loss: 0.0166%
Epoch [300/300], Step [184/225], Training Accuracy: 99.7198%, Training Loss: 0.0166%
Epoch [300/300], Step [185/225], Training Accuracy: 99.7128%, Tra

In [15]:
from playsound import playsound
playsound(u"sound.mp3")

In [16]:
# Test the model
model.eval()  # eval mode (batchnorm uses moving mean/variance instead of mini-batch mean/variance)
with torch.no_grad():
    correct = 0
    total = 0
    for X, Y in test_loader:
        X = X.to(device)
        Y = Y.to(device)
        outputs = model(X)
        _, predicted = torch.max(outputs.data, 1)
        total += Y.size(0)
        correct += (predicted == Y).sum().item()

    print('Test Accuracy : {} %'.format(100 * correct / total))

# Save the model checkpoint
#torch.save(model.state_dict(), 'model.ckpt')

Test Accuracy : 35.01945525291829 %
